In [ ]:
# Some of the code refered from: https://www.kaggle.com/svpons/feature-engineering

In [128]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns

# session

In [129]:
df_session = pd.read_csv('sessions.csv')

In [130]:
df_session.head(10)

user_id                 action action_type                action_detail  \
0  d1mm9tcy42                 lookup         NaN                          NaN   
1  d1mm9tcy42         search_results       click          view_search_results   
2  d1mm9tcy42                 lookup         NaN                          NaN   
3  d1mm9tcy42         search_results       click          view_search_results   
4  jpmpj40cvk                 lookup         NaN                          NaN   
5  jpmpj40cvk         search_results       click          view_search_results   
6  jpmpj40cvk         search_results       click          view_search_results   
7  jpmpj40cvk         search_results       click          view_search_results   
8  jpmpj40cvk         search_results       click          view_search_results   
9  jpmpj40cvk  ajax_refresh_subtotal       click  change_trip_characteristics   

       device_type  secs_elapsed  
0  Windows Desktop         319.0  
1  Windows Desktop       67753.0  
2  Windows Desktop         301.0  
3  Windows Desktop       22141.0  
4  Windows Desktop         957.0  
5  Windows Desktop         965.0  
6  Windows Desktop        1021.0  
7  Windows Desktop         938.0  
8  Windows Desktop        2702.0  
9  Windows Desktop         674.0

In [131]:
df_session.isnull().sum()

user_id            2797
action             7873
action_type      143097
action_detail    143097
device_type           0
secs_elapsed      11067
dtype: int64

In [132]:
df_session.action = df_session.action.fillna("NAN")
df_session.action_type = df_session.action_type.fillna("NAN")
df_session.action_detail = df_session.action_detail.fillna("NAN")
df_session.device_type = df_session.secs_elapsed.fillna("NAN")

In [133]:
df_session.action.value_counts()
df_session.action_type.value_counts()
df_session.action_detail.value_counts()
df_session.device_type.value_counts()

NAN          11067
0.0           7222
4.0           1920
3.0           1913
1.0           1844
2.0           1842
6.0           1812
5.0           1794
9.0           1792
7.0           1784
8.0           1772
23.0          1734
11.0          1727
10.0          1713
14.0          1713
13.0          1704
15.0          1693
20.0          1679
18.0          1660
19.0          1648
17.0          1646
12.0          1641
33.0          1621
27.0          1618
25.0          1602
16.0          1599
28.0          1598
21.0          1596
30.0          1584
39.0          1583
             ...  
98555.0          1
98557.0          1
98558.0          1
98561.0          1
360657.0         1
98502.0          1
98418.0          1
98498.0          1
98424.0          1
98431.0          1
98433.0          1
98434.0          1
98438.0          1
98439.0          1
98449.0          1
98451.0          1
98453.0          1
98454.0          1
98460.0          1
1671326.0        1
98467.0          1
98471.0     

In [134]:
# action values with low frequency are changed to "Other"

# threshold
act_freq = 100

act = dict(zip(*np.unique(df_session.action, return_counts=True)))
df_session.action = df_session.action.apply(lambda x : "Other" if act[x] < act_freq else x)

In [135]:
f_act = df_session.action.value_counts().argsort()
f_act_detail = df_session.action_detail.value_counts().argsort()
f_act_type = df_session.action_type.value_counts().argsort()
f_dev_type = df_session.device_type.value_counts().argsort()

In [136]:
print(f_act.size)
print(f_act_detail.size)
print(f_act_type.size)
print(f_dev_type.size)

117
108
10
114423


In [137]:
#group session by id.
dgr_sess = df_session.groupby(['user_id'])

In [138]:
len(dgr_sess)

15588

In [146]:
# loop on dgr_sess to create all the features
samples = []
count = 0
ln = len(dgr_sess)

for g in dgr_sess:
    gr = g[1] # date frame that contains all the data from eahc groupby value(user_id)
    
    l = []
    
    # the id
    l.append(g[0])
    
    # number of total actions
    l.append(len(gr))
    
    sev = gr.secs_elapsed.fillna(0).values
    
    #action features
    c_act = [0] * len(f_act)
    for i,v in enumerate(gr.action.values):
        c_act[f_act[v]] += 1
    _, c_act_uqc = np.unique(gr.action.values, return_counts=True)
    c_act += [len(c_act_uqc), np.mean(c_act_uqc), np.std(c_act_uqc)]
    l = l + c_act
    
    #action_detail features
    c_act_detail = [0] * len(f_act_detail)
    for i, v in enumerate(gr.action_detail.values):
        c_act_detail[f_act_detail[v]] += 1
    _, c_act_det_uqc = np.unique(gr.action_detail, return_counts=True)
    c_act_detail += [len(c_act_det_uqc), np.mean(c_act_det_uqc), np.std(c_act_det_uqc)]
    l = l + c_act_detail
    
    #action_type features
    #l_act_type = [0] * len(f_act_type)
    c_act_type = [0] * len(f_act_type)
    for i,v in enumerate(gr.action_type.values):
        #l_act_type[f_act_type[v]] += sev[i]
        c_act_type[f_act_type[v]] += 1
    #l_act_type = np.log(1 + np.array(l_act_type)).tolist()
    _, c_act_type_uqc = np.unique(gr.action_type.values, return_counts = True)
    c_act_type += [len(c_act_type_uqc), np.mean(c_act_type_uqc), np.std(c_act_type_uqc)]
    #1 = 1 + c_act_type + l_act_type
    l = l + c_act_type
    
    #device_type features
    c_dev_type = [0] * len(f_dev_type)
    for i,v in enumerate(gr.device_type.values):
        c_dev_type[f_dev_type[v]] += 1
    c_dev_type.append(len(np.unique(gr.device_type.values)))
    _, c_dev_type_uqc = np.unique(gr.device_type.values, return_counts = True)
    c_dev_type += [len(c_dev_type_uqc), np.mean(c_dev_type_uqc), np.std(c_dev_type_uqc)]
    l = l + c_dev_type
    
    #secs_elapsed features
    l_secs = [0] * 5
    l_log = [0] * 15
    if len(sev) > 0:
        #simpale statistics
        l_secs[0] = np.log(1 + np.sum(sev))
        l_secs[1] = np.log(1 + np.mean(sev))
        l_secs[2] = np.log(1 + np.std(sev))
        l_secs[3] = np.log(1 + np.median(sev))
        l_secs[4] = l_secs[0] / float(l[1])
        
        #values are grouped in 15 intervals
        log_sev = np.log(1 + sev).astype(int)
        l_log = np.bincount(log_sev, minlength = 15).tolist()
    l = l + l_secs + l_log
    
    samples.append(l)
    count += 1

In [142]:
f_dev_type

NAN          57211
0.0          76287
4.0          76286
3.0          76285
1.0          76284
2.0          76283
6.0          76282
5.0          76281
9.0          76280
7.0          76279
8.0          76278
23.0         76277
11.0         76276
10.0         76275
14.0         76274
13.0         76273
15.0         76272
20.0         76271
18.0         76270
19.0         76269
17.0         76268
12.0         76267
33.0         76266
27.0         76265
25.0         76288
16.0         76289
28.0         76290
21.0         76291
30.0         76315
39.0         76314
             ...  
98555.0         29
98557.0         28
98558.0         27
98561.0         26
360657.0        25
98502.0         24
98418.0         23
98498.0         22
98424.0         21
98431.0         20
98433.0         19
98434.0         18
98438.0         17
98439.0         16
98449.0         15
98451.0         14
98453.0         13
98454.0         12
98460.0         11
1671326.0       10
98467.0          9
98471.0     

In [147]:
samples

[['007gj7kqdk',
  9,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  3,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  2,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  6,
  1.5,
  0.76376261582597338,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,